In [9]:
import os, sys
sys.path.append('../src')
from copulae1 import *
from KDEs import *
from toolbox import *
import json
import datetime
import pickle

import matplotlib.pyplot as plt

In [10]:
# Gaussian, t_Copula, Clayton, Frank, Gumbel, Plackett, Gaussian mix Indep
C1  = Gaussian(dict(rho=0.9),       Law_RS=stats.norm, Law_RF=stats.norm)
C2  = t_Copula(dict(rho=0.1, nu=4), Law_RS=stats.norm, Law_RF=stats.norm, nu_lowerbound=2)
C2c = t_Copula(dict(rho=0.1, nu=4), Law_RS=stats.norm, Law_RF=stats.norm, nu_lowerbound=4)
C3  = Clayton(dict(theta=0.1),      Law_RS=stats.norm, Law_RF=stats.norm)
C4  = Frank(dict(theta=0.1),        Law_RS=stats.norm, Law_RF=stats.norm)
C5  = Gumbel(dict(theta=3),         Law_RS=stats.norm, Law_RF=stats.norm)
C6  = Plackett(dict(theta=10),      Law_RS=stats.norm, Law_RF=stats.norm)
C7  = Gaussian_Mix_Independent(dict(rho=.5,p=0.7),Law_RS=stats.norm, Law_RF=stats.norm)
C8  = rot180Gumbel(dict(theta=3), Law_RS=stats.norm, Law_RF=stats.norm)

In [11]:
calibration_method = 'MM'
q_arr = [0.05,0.1,0.9,0.95]

In [12]:
Copulae_names = ['Gaussian', 't_Copula', 't_Copula_Capped', 'Clayton', 'Frank', 'Gumbel', 'Plackett', 'Gauss Mix Indep', 'rotGumbel']
Copulae_arr = [C1, C2, C2c, C3, C4, C5, C6, C7, C8]
Copulae = dict(zip(Copulae_names, Copulae_arr))

In [13]:
paras_results = []
likelihood_results = []

spot_name = 'rs'
future_name = 'rf'
data_name = 'deribit_ETHUSD_BTCUSD'
data_path = '/Volumes/external_SSD/copulaData/Deribit_ready/ETHUSD_BTCUSD/'

ls = os.listdir(data_path + 'train/')
ls = [l for l in ls if l.endswith('.csv')]

In [13]:

start = 0

for i, file in enumerate(ls[start:]):
	print('-----', i, len(ls), str(datetime.datetime.now()), '-----')
	# Calibration
	train = pd.read_csv(data_path + 'train/' + file)
	spot = train.loc[:, spot_name]
	future = train.loc[:, future_name]
	u = ECDF(spot)(spot)
	v = ECDF(future)(future)

	kde_brr = KDE(spot, "Gaussian")
	kde_btc = KDE(future, "Gaussian")

	for C_name in Copulae:
		Copulae[C_name].Law_RS = kde_brr
		Copulae[C_name].Law_RF = kde_btc

	paras = []
	likelihood = []
	best_h = []
	for C_name in Copulae:
		if calibration_method == "MLE":
			Copulae[C_name].canonical_calibrate(u, v)

		elif calibration_method == "MM":
			Copulae[C_name].mm_calibrate(u, v, q_arr)

		print(C_name, 'is done.\n')

	for C_name in Copulae:
		paras.append((C_name, Copulae[C_name].paras))

	for C_name in Copulae:
		ln = Copulae[C_name].dependency_likelihood(u, v)
		likelihood.append((C_name, ln))

	paras_results.append(paras)
	likelihood_results.append(likelihood)

	if (i%60==0) or (i == 0) or (i==len(ls)):
		print('saved!')
		with open(data_name+'_paras.pickle', 'wb') as f:
			pickle.dump(paras_results, f)

		with open(data_name+'_likelihood.pickle', 'wb') as f:
			pickle.dump(likelihood_results, f)

----- 0 2116 2022-09-12 11:46:36.231154 -----
Optimization terminated successfully.
         Current function value: 0.011943
         Iterations: 33
         Function evaluations: 67
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.012135
         Iterations: 189
         Function evaluations: 364
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.012135
         Iterations: 174
         Function evaluations: 332
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.250013
         Iterations: 42
         Function evaluations: 93
Clayton is done.

Optimization terminated successfully.
         Current function value: 0.036611
         Iterations: 52
         Function evaluations: 114
Frank is done.

Optimization terminated successfully.
         Current function value: 0.122647
         Iterations: 36
         Function evaluations: 78
Gumbel is done.

Optimi

Optimization terminated successfully.
         Current function value: 0.009455
         Iterations: 67
         Function evaluations: 139
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.115932
         Iterations: 33
         Function evaluations: 72
rotGumbel is done.

----- 6 2116 2022-09-12 11:50:05.364520 -----
Optimization terminated successfully.
         Current function value: 0.020815
         Iterations: 31
         Function evaluations: 63
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.020849
         Iterations: 117
         Function evaluations: 227
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.020849
         Iterations: 113
         Function evaluations: 216
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.450210
         Iterations: 39
         Function evaluations: 86
Clayton is 

../src/copulae1.py:362: RuntimeWarning: invalid value encountered in power
  return A ** B


Optimization terminated successfully.
         Current function value: 0.021845
         Iterations: 169
         Function evaluations: 333
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.151858
         Iterations: 34
         Function evaluations: 74
rotGumbel is done.

----- 10 2116 2022-09-12 11:52:52.414612 -----
Optimization terminated successfully.
         Current function value: 0.022681
         Iterations: 30
         Function evaluations: 64
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.025144
         Iterations: 39
         Function evaluations: 149
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.022933
         Iterations: 123
         Function evaluations: 285
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.441237
         Iterations: 33
         Function evaluations: 74
Clayton is

Optimization terminated successfully.
         Current function value: 0.011127
         Iterations: 69
         Function evaluations: 144
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.137389
         Iterations: 35
         Function evaluations: 75
rotGumbel is done.

----- 16 2116 2022-09-12 11:57:00.609690 -----
Optimization terminated successfully.
         Current function value: 0.003913
         Iterations: 31
         Function evaluations: 65
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.003857
         Iterations: 127
         Function evaluations: 271
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.003857
         Iterations: 125
         Function evaluations: 266
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.327056
         Iterations: 38
         Function evaluations: 86
Clayton is

...

Optimization terminated successfully.
         Current function value: 0.009104
         Iterations: 68
         Function evaluations: 141
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.107363
         Iterations: 33
         Function evaluations: 72
rotGumbel is done.

----- 2090 2116 2022-09-13 03:34:25.610363 -----
Optimization terminated successfully.
         Current function value: 0.021868
         Iterations: 32
         Function evaluations: 67
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.021942
         Iterations: 125
         Function evaluations: 240
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.021942
         Iterations: 130
         Function evaluations: 246
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.410682
         Iterations: 37
         Function evaluations: 80
Clayton 

Optimization terminated successfully.
         Current function value: 0.021188
         Iterations: 127
         Function evaluations: 248
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.150927
         Iterations: 34
         Function evaluations: 75
rotGumbel is done.

----- 2096 2116 2022-09-13 03:38:23.290312 -----
Optimization terminated successfully.
         Current function value: 0.021250
         Iterations: 30
         Function evaluations: 63
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.021346
         Iterations: 110
         Function evaluations: 228
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.021346
         Iterations: 93
         Function evaluations: 193
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.426693
         Iterations: 36
         Function evaluations: 81
Clayton 

Optimization terminated successfully.
         Current function value: 0.028693
         Iterations: 97
         Function evaluations: 183
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.167677
         Iterations: 33
         Function evaluations: 74
rotGumbel is done.

----- 2102 2116 2022-09-13 03:41:54.332586 -----
Optimization terminated successfully.
         Current function value: 0.028639
         Iterations: 30
         Function evaluations: 64
Gaussian is done.

t_Copula is done.

t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.429331
         Iterations: 35
         Function evaluations: 77
Clayton is done.

Optimization terminated successfully.
         Current function value: 0.050634
         Iterations: 36
         Function evaluations: 81
Frank is done.

Optimization terminated successfully.
         Current function value: 0.014283
         Iterations: 32
         Fun

Optimization terminated successfully.
         Current function value: 0.021242
         Iterations: 119
         Function evaluations: 227
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.150868
         Iterations: 35
         Function evaluations: 76
rotGumbel is done.

----- 2108 2116 2022-09-13 03:46:39.068317 -----
Optimization terminated successfully.
         Current function value: 0.036171
         Iterations: 32
         Function evaluations: 67
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.036181
         Iterations: 102
         Function evaluations: 202
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.036181
         Iterations: 102
         Function evaluations: 208
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.451800
         Iterations: 37
         Function evaluations: 83
Clayton

Optimization terminated successfully.
         Current function value: 0.021194
         Iterations: 140
         Function evaluations: 261
Gauss Mix Indep is done.

Optimization terminated successfully.
         Current function value: 0.150871
         Iterations: 32
         Function evaluations: 72
rotGumbel is done.

----- 2114 2116 2022-09-13 03:50:44.304764 -----
Optimization terminated successfully.
         Current function value: 0.024063
         Iterations: 30
         Function evaluations: 65
Gaussian is done.

Optimization terminated successfully.
         Current function value: 0.024194
         Iterations: 38
         Function evaluations: 151
t_Copula is done.

Optimization terminated successfully.
         Current function value: 0.024183
         Iterations: 104
         Function evaluations: 209
t_Copula_Capped is done.

Optimization terminated successfully.
         Current function value: 0.427637
         Iterations: 35
         Function evaluations: 79
Clayton 

In [30]:
# with open(data_name+'_paras.pickle', 'wb') as f:
#     pickle.dump(paras_results, f)

# with open(data_name+'_likelihood.pickle', 'wb') as f:
#     pickle.dump(likelihood_results, f)


# with open(data_name+'_likelihood.pickle', 'rb') as f:
#     likelihood_results = pickle.load(f)
    
# with open(data_name+'_paras.pickle', 'rb') as f:
#     paras_results = pickle.load(f)


with open(data_name+'_paras_dict.pickle', 'wb') as f:
    pickle.dump(paras_results_dict, f)

with open(data_name+'_likelihood_dict.pickle', 'wb') as f:
    pickle.dump(likelihood_results_dict, f)

In [24]:
paras_results_dict = dict(zip(ls, paras_results))
likelihood_results_dict = dict(zip(ls, likelihood_results))

In [27]:
file = '1032.csv'
train = pd.read_csv(data_path + 'train/' + file)
spot = train.loc[:, spot_name]
future = train.loc[:, future_name]
u = ECDF(spot)(spot)
v = ECDF(future)(future)
for C_name in Copulae:
    Copulae[C_name].mm_calibrate(u, v, q_arr)

paras = []
for C_name in Copulae:
    paras.append((C_name, Copulae[C_name].paras))

Optimization terminated successfully.
         Current function value: 0.012874
         Iterations: 31
         Function evaluations: 66
Optimization terminated successfully.
         Current function value: 0.031014
         Iterations: 39
         Function evaluations: 155
Optimization terminated successfully.
         Current function value: 0.030938
         Iterations: 40
         Function evaluations: 159
Optimization terminated successfully.
         Current function value: 0.401002
         Iterations: 39
         Function evaluations: 85
Optimization terminated successfully.
         Current function value: 0.038158
         Iterations: 40
         Function evaluations: 92
Optimization terminated successfully.
         Current function value: 0.034154
         Iterations: 35
         Function evaluations: 77
Optimization terminated successfully.
         Current function value: 0.014947
         Iterations: 40
         Function evaluations: 91


../src/copulae1.py:362: RuntimeWarning: invalid value encountered in power
  return A ** B


Optimization terminated successfully.
         Current function value: 0.012046
         Iterations: 147
         Function evaluations: 273
Optimization terminated successfully.
         Current function value: 0.147986
         Iterations: 36
         Function evaluations: 77


In [28]:
paras

[('Gaussian', {'rho': 0.7820099808874359}),
 ('t_Copula', {'rho': 0.8326797893360046, 'nu': 87.26513210333272}),
 ('t_Copula_Capped', {'rho': 0.8325760440411243, 'nu': 87.26513210332058}),
 ('Clayton', {'theta': 1.558073353937239}),
 ('Frank', {'theta': 12.17513785344805}),
 ('Gumbel', {'theta': 2.227588771162202}),
 ('Plackett', {'theta': 25.157979066710638}),
 ('Gauss Mix Indep', {'rho': 0.7801980444893992, 'p': 0.9989999999999889}),
 ('rotGumbel', {'theta': 2.2432121039308415})]

In [29]:
paras_results_dict[file]

[('Gaussian', {'rho': 0.7820099802755033}),
 ('t_Copula', {'rho': 0.792454845566543, 'nu': 87.26513210323297}),
 ('t_Copula_Capped', {'rho': 0.8494868922707599, 'nu': 87.26513210333398}),
 ('Clayton', {'theta': 1.5580733221783978}),
 ('Frank', {'theta': 12.175124075725694}),
 ('Gumbel', {'theta': 2.227588755515863}),
 ('Plackett', {'theta': 25.157974110380792}),
 ('Gauss Mix Indep', {'rho': 0.7802003832325097, 'p': 0.9989999999998811}),
 ('rotGumbel', {'theta': 2.2432121003656924})]

In [ ]:
# Prettify the result
c_arr = []
date_range_arr = []
for i, file in enumerate(ls):
	train = pd.read_csv(data_path + 'train/' + file)
	date_range = train.timestamp.iloc[-1] + ' to ' + train.timestamp.iloc[0]
	date_range_arr.append(date_range)

	c = pd.DataFrame(paras_results[i])
	c.index = c.iloc[:, 0]
	c = pd.DataFrame(c.iloc[:, 1])
	c_arr.append(c)

paras_results_pd = pd.concat(dict(zip(ls, c_arr)), axis=1)
paras_results_pd.columns = paras_results_pd.columns.droplevel(1)
paras_results_pd.index.name = None

l_arr = []
date_range_arr = []
for i, file in enumerate(list(paras_results_pd.columns)):
	train = pd.read_csv(data_path + 'train/' + file)
	date_range = train.timestamp.iloc[-1] + ' to ' + train.timestamp.iloc[0]
	date_range_arr.append(date_range)

	c = pd.DataFrame(likelihood_results[i])
	c.index = c.iloc[:, 0]
	c = pd.DataFrame(c.iloc[:, 1])
	l_arr.append(c)

likelihood_results_pd = pd.concat(dict(zip(ls, l_arr)), axis=1)
likelihood_results_pd.columns = likelihood_results_pd.columns.droplevel(1)
likelihood_results_pd.index.name = None

In [ ]:
# Save results as html for display
display_paras = paras_results_pd.copy()
display_paras.columns = date_range_arr
display_paras = display_paras.reindex(sorted(display_paras.columns), axis=1)

display_likelihood = likelihood_results_pd.copy()
display_likelihood.columns = date_range_arr
display_likelihood = display_likelihood.reindex(sorted(display_likelihood.columns), axis=1)

# Save files to designated directories
if not os.path.exists("../results/" + data_name):
	print("Create new folder for results")
	os.mkdir("../results/" + data_name)
	os.mkdir("../results/" + data_name + "/MLE")
	os.mkdir("../results/" + data_name + "/MM")

if calibration_method == "MLE":
	path = "../results/" + data_name + "/MLE/"
	paras_results_pd.to_json(path + "parameters.json")
	likelihood_results_pd.to_json(path + "likelihood.json")

	display_paras.to_html(path + "paras.html")
	display_likelihood.to_html(path + "likelihood.html")

elif calibration_method == "MM":
	path = "../results/" + data_name + "/MM/"
	paras_results_pd.to_json(path + "parameters.json")
	likelihood_results_pd.to_json(path + "likelihood.json")

	display_paras.to_html(path + "paras.html")
	display_likelihood.to_html(path + "likelihood.html")

print('Done')